### 获取测试数据

In [1]:
'''
    从es里读取的content是html格式，需要解析成文本
'''
def sentencesMaker(html):
    sentences = []
    if not html or not html.strip():
        return sentences
    try:
        from html.parser import unescape
        html = unescape(html)

        import justext
        paragraphs = justext.justext(html, [])

        cache_sentences = ''

        for p in paragraphs:
            sent = p.text.strip().replace('\xa0', '').replace('\u3000', '')
            sent = sent.encode('gb2312', 'ignore').decode('gb2312').encode('gbk', 'ignore').decode('gbk')
            if not sent:
                continue

            # 可能是含有名字，需要进一步处理
            if len(cache_sentences) < 5:
                cache_sentences += ' ' + sent
            else:
                sentences.append(cache_sentences.strip())
                cache_sentences = sent

        if not not cache_sentences:
            sentences.append(cache_sentences.strip())
    except Exception as e:
        logger.error(e)

    return sentences

In [2]:
'''
    连接es
'''
from elasticsearch import Elasticsearch
from elasticsearch import helpers

es = Elasticsearch('http://ip:port')

In [12]:
from elasticsearch import helpers

# def search_bl2(from_number, off_size):
def search_bl2():
    es_search_options = set_search_optional_bl2()
    es_result = get_search_result(query=es_search_options, index="toutiao_bl2")
    return es_result


def get_search_result(query, index):
    es_result = helpers.scan(
        es,
        query=query,
        index=index,
        doc_type='news',
        scroll="10m",
        timeout='10m'
    )
    return es_result


def set_search_optional_bl2(): 
    es_search_options = {
   "query": {
    
    "match_all": {}
  }
  }
    return es_search_options

In [18]:
all_results_bl2 = search_bl2() # 不能用list，数据量太大，内存会溢出

### 分词/去停用词/去特殊符号

In [6]:
import jieba
import jieba.posseg as psg

jieba.load_userdict("../train model/user_dict.txt")

import zhon.hanzi
chi_char = zhon.hanzi.punctuation

import string
eng_char = string.punctuation

with open("../train model/stop_words.utf8", "r", encoding="utf-8") as stop_word:
    stop_words = stop_word.readlines()
    
from sklearn.externals import joblib

tfidf = joblib.load("../train model/tfidf_vect_business.pkl")
svm = joblib.load("../train model/svm_business.pkl")

Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache
Loading model cost 0.942 seconds.
Prefix dict has been built succesfully.


### 测试数据

In [22]:
Y = []
i = 0

from functools import reduce

for item in all_results_bl2:
    
    if item:  # 从es中获取的结果不为空
        i += 1
        print(i)
        title_content = item["_source"]["title"] + "。" + ''.join(sentencesMaker(item["_source"]["content"]))
        
        if title_content:  # 从es获取的结果中抽取的title+content不为空
            token_text = [w.word for w in psg.cut(title_content) if w.flag.startswith('n') 
                          and w.word not in stop_words and w.word not in chi_char and w.word not in eng_char]
            
            if token_text: # title+content分词再筛选之后不为空
                token_text = [reduce(lambda x,y:str(x)+ " " +str(y), token_text)]

                test_features = tfidf.transform(token_text)

                y_prediction = svm.predict(test_features)
                print(y_prediction)
                print("*****************************************")

                Y.extend(y_prediction.tolist())
            else:
                continue
        else:
            continue
    else:
        continue
    
print(i)

1
['1']
*****************************************
2
['1']
*****************************************
3
['1']
*****************************************
4
['1']
*****************************************
5
['1']
*****************************************
6
['1']
*****************************************
7
['0']
*****************************************
8
['1']
*****************************************
9
['0']
*****************************************
10
['1']
*****************************************
11
['1']
*****************************************
12
['1']
*****************************************
13
['0']
*****************************************
14
['1']
*****************************************
15
['1']
*****************************************
16
['1']
*****************************************
17
['1']
*****************************************
18
['1']
*****************************************
19
['1']
*****************************************
20
['1']
*******************************

['1']
*****************************************
162
['0']
*****************************************
163
['0']
*****************************************
164
['1']
*****************************************
165
['1']
*****************************************
166
['1']
*****************************************
167
['1']
*****************************************
168
['0']
*****************************************
169
['1']
*****************************************
170
['1']
*****************************************
171
['1']
*****************************************
172
['1']
*****************************************
173
['1']
*****************************************
174
['0']
*****************************************
175
['1']
*****************************************
176
['1']
*****************************************
177
['1']
*****************************************
178
['1']
*****************************************
179
['1']
*****************************************
180
['1']
******

['1']
*****************************************
324
['1']
*****************************************
325
['1']
*****************************************
326
['1']
*****************************************
327
['1']
*****************************************
328
['1']
*****************************************
329
['1']
*****************************************
330
['1']
*****************************************
331
['1']
*****************************************
332
['1']
*****************************************
333
['1']
*****************************************
334
['1']
*****************************************
335
['1']
*****************************************
336
['1']
*****************************************
337
['1']
*****************************************
338
['1']
*****************************************
339
['1']
*****************************************
340
['1']
*****************************************
341
['1']
*****************************************
342
['1']
******

['1']
*****************************************
483
['1']
*****************************************
484
['1']
*****************************************
485
['1']
*****************************************
486
['1']
*****************************************
487
['1']
*****************************************
488
['1']
*****************************************
489
['1']
*****************************************
490
['1']
*****************************************
491
['1']
*****************************************
492
['1']
*****************************************
493
['1']
*****************************************
494
['1']
*****************************************
495
['0']
*****************************************
496
['1']
*****************************************
497
['1']
*****************************************
498
['1']
*****************************************
499
['1']
*****************************************
500
['0']
*****************************************
501
['1']
******

['1']
*****************************************
641
['1']
*****************************************
642
['1']
*****************************************
643
['1']
*****************************************
644
['1']
*****************************************
645
['1']
*****************************************
646
['1']
*****************************************
647
['1']
*****************************************
648
['1']
*****************************************
649
['0']
*****************************************
650
['1']
*****************************************
651
['0']
*****************************************
652
['0']
*****************************************
653
['1']
*****************************************
654
['1']
*****************************************
655
['0']
*****************************************
656
['1']
*****************************************
657
['1']
*****************************************
658
['0']
*****************************************
659
['1']
******

...

['1']
*****************************************
109341
['1']
*****************************************
109342
['1']
*****************************************
109343
['0']
*****************************************
109344
['1']
*****************************************
109345
['0']
*****************************************
109346
['1']
*****************************************
109347
['1']
*****************************************
109348
['0']
*****************************************
109349
['1']
*****************************************
109350
['1']
*****************************************
109351
['1']
*****************************************
109352
['1']
*****************************************
109353
['1']
*****************************************
109354
['1']
*****************************************
109355
['1']
*****************************************
109356
['1']
*****************************************
109357
['1']
*****************************************
109358
['1']
****

['1']
*****************************************
109494
['0']
*****************************************
109495
['1']
*****************************************
109496
['1']
*****************************************
109497
['1']
*****************************************
109498
['1']
*****************************************
109499
['1']
*****************************************
109500
['1']
*****************************************
109501
['0']
*****************************************
109502
['1']
*****************************************
109503
['1']
*****************************************
109504
['1']
*****************************************
109505
['0']
*****************************************
109506
['0']
*****************************************
109507
['1']
*****************************************
109508
['0']
*****************************************
109509
['0']
*****************************************
109510
['1']
*****************************************
109511
['1']
****

['0']
*****************************************
109645
['1']
*****************************************
109646
['1']
*****************************************
109647
['1']
*****************************************
109648
['0']
*****************************************
109649
['1']
*****************************************
109650
['1']
*****************************************
109651
['0']
*****************************************
109652
['0']
*****************************************
109653
['1']
*****************************************
109654
['1']
*****************************************
109655
['1']
*****************************************
109656
['1']
*****************************************
109657
['0']
*****************************************
109658
['1']
*****************************************
109659
['1']
*****************************************
109660
['1']
*****************************************
109661
['1']
*****************************************
109662
['1']
****

['0']
*****************************************
109797
['1']
*****************************************
109798
['1']
*****************************************
109799
['0']
*****************************************
109800
['1']
*****************************************
109801
['1']
*****************************************
109802
['1']
*****************************************
109803
['1']
*****************************************
109804
['1']
*****************************************
109805
['1']
*****************************************
109806
['0']
*****************************************
109807
['1']
*****************************************
109808
['1']
*****************************************
109809
['1']
*****************************************
109810
['1']
*****************************************
109811
['1']
*****************************************
109812
['1']
*****************************************
109813
['1']
*****************************************
109814
['1']
****

['1']
*****************************************
109947
['1']
*****************************************
109948
['0']
*****************************************
109949
['1']
*****************************************
109950
['1']
*****************************************
109951
['1']
*****************************************
109952
['1']
*****************************************
109953
['1']
*****************************************
109954
['1']
*****************************************
109955
['1']
*****************************************
109956
['1']
*****************************************
109957
['1']
*****************************************
109958
['0']
*****************************************
109959
['1']
*****************************************
109960
['1']
*****************************************
109961
['1']
*****************************************
109962
['1']
*****************************************
109963
['1']
*****************************************
109964
['1']
****

In [23]:
len(Y)

109991

In [24]:
nlabel, plabel = 0, 0
for i in Y:
    if i == "0":
        plabel += 1
    else:
        nlabel += 1
print("头条正样本", plabel, plabel/(plabel + nlabel))
print("头条负样本", nlabel, nlabel/(plabel + nlabel))

头条正样本 16770 0.15246702002891147
头条负样本 93221 0.8475329799710886


In [ ]:
'''
    
#  109991
头条正样本 16770 0.15246702002891147
头条负样本 93221 0.8475329799710886

# 160706
百度正样本 48235 0.30014436299827013
百度负样本 112471 0.6998556370017298

# 25859
微信正样本 4002 0.1547623651339959
微信负样本 21857 0.8452376348660041

# 10794
36kr正样本 2385 0.22095608671484157
36kr负样本 8409 0.7790439132851584

# total 307350
average正样本 0.2322824141857817
average负样本 0.7677175858142183
    
'''
